In [ ]:
!pip install torch
!pip3 install Cython
!pip install pdfreader
!pip install pdfreader
!pip install sentence_transformers
!pip install ipywidgets
!pip install download
!pip install spacy
!pip install nltk
!pip install contractions
!pip install inflect
!pip install docx2txt

In [2]:
import warnings
warnings.filterwarnings('ignore')

In [3]:
from transformers import GPT2Tokenizer, T5ForConditionalGeneration
from sentence_transformers.cross_encoder import CrossEncoder
from sentence_transformers import SentenceTransformer
from transformers import AutoModel, AutoTokenizer 
from subprocess import run, STDOUT, PIPE
from nltk.tokenize import word_tokenize
from pdfreader import SimplePDFViewer
from nltk.corpus import stopwords
import clickhouse_connect
import contractions
import numpy as np
import unicodedata
import subprocess
import requests
import datetime
import inflect
import torch
import spacy
import emoji
import nltk
import os
import re


import chardet

from pdfminer.pdfparser import PDFParser
from pdfminer.pdfdocument import PDFDocument
import datetime

nltk.download('stopwords')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/zoidberg2000/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /home/zoidberg2000/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [29]:
def set_to_master(client, id, id_doc, chunk):
    client.insert('ML_unitaz', [id, id_doc, chunk], column_names=['id', 'id_document', 'chunk'])

def set_to_slave(client, id, document_name, document_url):
    client.insert('ML_skibidi', [id, document_name, document_url], column_names=['id', 'document_name', 'document_url'])

def set_to_db(client, data):
    client.insert('test_table', data, column_names=['id', 'document_url', "chunk_number", 'chunk_array', "chunk_text"])


def get_chunk(client, table, id):
    arr_chunk = client.query(f'SELECT chunk FROM {table} WHERE id = {id}')
    return arr_chunk.result_rows[0][0]


def get_row(client, id):
    data1 = client.query(f'SELECT * EXCEPT (id) FROM ML_skibidi WHERE id = {id}')
    data2 = client.query(f'SELECT * EXCEPT (id) FROM ML_unitaz WHERE id = {id}')
    if data1 != None and data2 != None:
        result = data1.result_rows[0] + (data2.result_rows[0])
        return result
    else:
        return None

def date_fix(date_bin: str):
    fix_date = date_bin[4:17]
    fix_date = datetime.datetime.strptime(fix_date, "%Y%m%d%H%M%S")
    return str(fix_date)

def get_metadata(file_path):
    file_path = "docs_new/" + file_path
    with open(file_path, "rb") as fp:
        # enc = chardet.detect(text).get("encoding")
        try:
            parser = PDFParser(fp)
        except:
            return ["None", "None"]
        doc = PDFDocument(parser)
        try:
            create_date = date_fix(str(doc.info[0]["CreationDate"]))
        except:
            create_date = "none"
        try:
            mod_date = date_fix(str(doc.info[0]["ModDate"]))
        except:
            create_date = "none"
    return [create_date, mod_date]

def get_link(file_path):
    with open("download_info_new.txt", "r") as fp:
        lines = fp.readlines()
        for line in lines:
            if file_path in line:
                match = re.search(r'Ссылка: (.*)', line)
                if match:
                    link_text = match.group(1)
                    return link_text

In [25]:
client = clickhouse_connect.get_client(host='localhost', port=8123, username='default', password='')

In [32]:
client.command(
    f"CREATE TABLE test_table (id UInt32, document_name String, document_url String, create_date String, modification_date String, chunk_number UInt32, chunk_embeding Array(Float32), chunk_text String) ENGINE Memory"
)

In [9]:
vmodel = SentenceTransformer('intfloat/multilingual-e5-large-instruct')


In [31]:
client.command("DROP TABLE test_table")

In [ ]:
reader = Reader()
id = 1

for filename in os.listdir("docs_new"):
    try:
        text = reader.read_file(filename)
        file_url = get_link(filename)
        metadata = get_metadata(filename)
        create_date = metadata[0]
        modification_date = metadata[1]
        if text != "":
            encoder = Encoder(text,vmodel)
            encoder.encode_document()
            for key, value in encoder.encoded_text_by_chunks.items():
                chunk_text=encoder.dict_by_chunks[key]
                print([[id, filename, file_url, create_date, modification_date, key, value, chunk_text]])
                client.insert(
                    "test_table",
                    [[id, filename, file_url, create_date, modification_date, key, value, chunk_text]],
                    column_names=[
                        "id",
                        "document_name",
                        "document_url",
                        "create_date",
                        "modification_date", "chunk_number",
                        "chunk_embeding",
                        "chunk_text"
                    ],
                )
        id += 1
    except Exception as ex:
        print(ex)

/tmp/ipykernel_26245/475254136.py:6: RuntimeWarning: invalid value encountered in divide
  vecs = np.stack([sent.vector / sent.vector_norm for sent in sents])


8
{1: 'центральный банк российской федерации банк россии one hundred and seven thousand and sixteen москва ул неглинная twelve тел four hundred and ninetynine three million  three thousand eight eight hundred three million  three thousand информационное письмо банка россии отмене информационного письма банка россии nine марта two thousand and sixteen года ин053511 кредитным организациям структурным подразделениям банка россии списку рассылки банк россии сообщает связи пересмотром подходов установлению национальной антициклической надбавки1 даты размещения настоящего информационного письма банка россии официальном сайте банка россии информационнотелекоммуникационной сети интернет отменяется информационное письмо банка россии nine марта two thousand and sixteen года ин053511 методиках моделях используемых банком россии определении величины национальной антициклической надбавки нормативам достаточности собственных средств капитала дальнейшем принятии решения установлении национальной анти

[[1, '20240216_in-018-35_12.PDF', 'https://www.cbr.ru/Crosscut/LawActs/File/7682', '2024-02-16 10:29:04', '2024-02-16 10:29:04', 1, array([ 0.03061877, -0.01087979, -0.026966  , ..., -0.0163132 ,
       -0.01196628,  0.00250367], dtype=float32), 'центральный банк российской федерации банк россии one hundred and seven thousand and sixteen москва ул неглинная twelve тел four hundred and ninetynine three million  three thousand eight eight hundred three million  three thousand информационное письмо банка россии отмене информационного письма банка россии nine марта two thousand and sixteen года ин053511 кредитным организациям структурным подразделениям банка россии списку рассылки банк россии сообщает связи пересмотром подходов установлению национальной антициклической надбавки1 даты размещения настоящего информационного письма банка россии официальном сайте банка россии информационнотелекоммуникационной сети интернет отменяется информационное письмо банка россии nine марта two thousand an

15
{1: 'центральный банк российской федерации банк россии one hundred and seven thousand and sixteen москва ул неглинная д twelve тел four hundred and ninetynine three million  three thousand eight eight hundred three million  three thousand информационное письмо банка россии порядке отражения уникального идентификатора договора сделки источникам формирования кредитных историй бюро кредитных историй eleven million  seventytwo thousand and twentyfour вступают силу изменения закон 218фз1 внесенные законом 295фз2 согласно которым источники3 должны будут указывать договоре займа кредита договоре поручительства заключаемых источником заемщиком поручителем договоре заключаемом принципалом предоставлении независимой гарантии либо независимой гарантии также иных договорах информация обязательствах которым передается бюро4 далее совместном упоминании договор уникальный идентификатор договора сделки далее уид сделки присвоенный источником договору целях унификации практик размещения информации у

[[2, '20240213_ in-014-46_11.pdf', 'https://www.cbr.ru/Crosscut/LawActs/File/7681', '2024-02-13 12:07:02', '2024-02-13 12:07:02', 1, array([ 0.02425116, -0.01048145, -0.03124342, ..., -0.02411441,
       -0.03504973, -0.01488168], dtype=float32), 'центральный банк российской федерации банк россии one hundred and seven thousand and sixteen москва ул неглинная д twelve тел four hundred and ninetynine three million  three thousand eight eight hundred three million  three thousand информационное письмо банка россии порядке отражения уникального идентификатора договора сделки источникам формирования кредитных историй бюро кредитных историй eleven million  seventytwo thousand and twentyfour вступают силу изменения закон 218фз1 внесенные законом 295фз2 согласно которым источники3 должны будут указывать договоре займа кредита договоре поручительства заключаемых источником заемщиком поручителем договоре заключаемом принципалом предоставлении независимой гарантии либо независимой гарантии также 

...

27
1
{}


4
{1: 'four hundred and ninetyfive seven million  seven hundred and nineteen thousand  one hundred информационное письмо отмене указания оперативного характера банка россии twentyseven июня two thousand and two года 82т департамент надзора системно значимыми кредитными организациями территориальные учреждения банка россии связи вступлением силу указания банка россии twentyseven декабря two thousand and eighteen года 5045у порядке взаимодействия центрального банка российской федерации федеральной налоговой службы вопросам государственной регистрации кредитных организаций государственной регистрации изменений внесенных устав кредитной организации внесения изменений сведения кредитной организации содержащиеся едином государственном реестре юридических лиц связанных внесением изменений устав государственной регистрации изменений внесенных устав микрофинансовой компании связи получением статуса кредитной организации государственной регистрации изменений внесенных устав юридического лица свя

13
1
{}


6
{1: 'центральный банк российской федерации банк россии one hundred and seven thousand and sixteen москва ул неглинная twelve тел four hundred and ninetyfive seven million  seven hundred and nineteen thousand  one hundred two twentyeight million  twentytwo thousand and nineteen ин061419 особенностях применения инструкции банка россии thirty million  fiftytwo thousand and fourteen 153и территориальным учреждениям банка россии кредитным организациям временная администрация назначенная банком россии отзыва аннулирования лицензии финансовой организации кредитной организации страховой организации негосударственного пенсионного фонда управляющей компании инвестиционного фонда паевого инвестиционного фонда негосударственного пенсионного фонда специализированного депозитария далее временная администрация исполняющая функции единоличного исполнительного органа действует силу законодательства российской федерации регулирующего деятельность пунктами fortyone four hundred and thirteen инструкции 

[[1226, '20190228_in_06_14-19.pdf', 'https://www.cbr.ru/Crosscut/LawActs/File/2360', '2019-03-01 14:38:01', '2019-03-05 14:53:05', 1, array([ 0.02560687, -0.00437773, -0.02605636, ..., -0.02180004,
       -0.01991706,  0.00514126], dtype=float32), 'центральный банк российской федерации банк россии one hundred and seven thousand and sixteen москва ул неглинная twelve тел four hundred and ninetyfive seven million  seven hundred and nineteen thousand  one hundred two twentyeight million  twentytwo thousand and nineteen ин061419 особенностях применения инструкции банка россии thirty million  fiftytwo thousand and fourteen 153и территориальным учреждениям банка россии кредитным организациям временная администрация назначенная банком россии отзыва аннулирования лицензии финансовой организации кредитной организации страховой организации негосударственного пенсионного фонда управляющей компании инвестиционного фонда паевого инвестиционного фонда негосударственного пенсионного фонда специализир

In [ ]:
nlp = spacy.load('ru_core_news_lg')

In [20]:

# Load the Spacy model

def process(text):
    doc = nlp(text)
    sents = list(doc.sents)
    vecs = np.stack([sent.vector / sent.vector_norm for sent in sents])
    print(len(sents))
    return sents, vecs

def cluster_text(sents, vecs, threshold):
    clusters = [[0]]
    for i in range(1, len(sents)):
        if np.dot(vecs[i], vecs[i-1]) < threshold:
            clusters.append([])
        clusters[-1].append(i)

    return clusters

def clean_text(input_text):    
    clean_text = re.sub('<[^<]+?>', '', input_text)
    clean_text = re.sub(r'http\S+', '', clean_text)
    clean_text = clean_text.lower()
    clean_text = re.sub('\s+', ' ', clean_text)
    clean_text = re.sub('[^а-яА-Я0-9\s]', '', clean_text)
    temp = inflect.engine()
    words = []
    for word in clean_text.split():
        if word.isdigit():
            words.append(temp.number_to_words(word))
        else:
            words.append(word)
    clean_text = ' '.join(words)

    stop_words = set(stopwords.words('russian'))
    tokens = word_tokenize(clean_text)
    tokens = [token for token in tokens if token not in stop_words]
    clean_text = ' '.join(tokens)

    clean_text = re.sub(r'[^\w\s]', '', clean_text)

    return clean_text


def get_chunks_dict(text):
    clusters_lens = []
    final_texts = []
    
    threshold = 0.3
    sents, vecs = process(text)
    
    clusters = cluster_text(sents, vecs, threshold)
    
    for cluster in clusters:
        cluster_txt = clean_text(' '.join([sents[i].text for i in cluster]))
        cluster_len = len(cluster_txt)
    
        if cluster_len < 350:
            continue
    
        elif cluster_len > 3500:
            threshold = 0.6
            sents_div, vecs_div = process(cluster_txt)
            reclusters = cluster_text(sents_div, vecs_div, threshold)
    
            for subcluster in reclusters:
                div_txt = clean_text(' '.join([sents_div[i].text for i in subcluster]))
                div_len = len(div_txt)
    
                if div_len < 350 or div_len > 3500:
                    continue
    
                clusters_lens.append(div_len)
                final_texts.append(div_txt)
    
        else:
            clusters_lens.append(cluster_len)
            final_texts.append(cluster_txt)
    
    chunks = {}
    for i in range(0, len(clusters_lens)):
      chunks[i+1] = final_texts[i]

    return chunks


In [6]:
class Reader:
    def read_file(self, filename):
        
        if filename.lower().endswith(".doc"):
        
            cmd = f'/bin/antiword {os.getcwd()}/docs_new/ves091230078.doc'
            
            file_text = run(cmd.split(), stdout=PIPE, stderr=STDOUT, text=True)
        
        else:
        
            with open(os.getcwd() + "/docs_new/" + filename, "rb") as file:
            
                if filename.lower().endswith(".pdf"):
                    
                    viewer = SimplePDFViewer(file)
                    
                    file_text = ""
                    
                    for canvas in viewer:
        
                        file_text += "".join(canvas.strings)
            
            if file_text[:50].isascii():
                
                file_text = ""
                
        return file_text

In [13]:
class DocumentHolder:
    try:
        
        os.mkdir("docs")
    
    except:
    
        pass

    N = len(os.listdir("docs"))

    def __init__(self, url) -> None:
        self.url = url
        self.text = ""
        self.load_doc()
        self.read_file()

    def load_doc(self):
        
        try:
        
            subprocess.call(f"curl -o docs/{self.N}.pdf {self.url}", shell=True, executable="/bin/bash")
            
            self.filename = f"{self.N}.pdf"
            
            self.N += 1
        
        except Exception as ex:
        
            print(ex)

    def read_file(self):
        
        self.fd = open("docs/" + self.filename,  "rb")
        
        self.viewer = SimplePDFViewer(self.fd)

        for canvas in self.viewer:

            self.text += "".join(canvas.strings)


class Encoder:
    def __init__(self, doc_text: str, model, chunk_size: int = 1) -> None:
        self.doc_text = doc_text
        self.dict_by_chunks = get_chunks_dict(self.doc_text)
        self.document_name = ""
        self.encoded_text_by_chunks = self.dict_by_chunks.copy()
        self.model = model

    def encode_document(self) -> dict[int, list[float]]:
        print(self.dict_by_chunks)
        for chunk_num in self.dict_by_chunks:
        
            embedding = self.model.encode(self.dict_by_chunks[chunk_num], normalize_embeddings=True)
            
            self.encoded_text_by_chunks[chunk_num] = embedding
            
        return self.encoded_text_by_chunks

    def encode_query(self, query: str) -> list[float]:
        
        return self.model.encode(query)


class VectorCalculator:
    def __init__(self, encoded_query, encoded_document_by_chunks: dict[int, str]) -> None:
        self.encoded_query = encoded_query
        self.encoded_document_by_chunks = encoded_document_by_chunks
        self.scores = []

    def get_score_by_chunk(self, chunk_num) -> float:
        
        vec = self.encoded_document_by_chunks[chunk_num]
        
        return vec @ self.encoded_query / np.linalg.norm(vec)

    def get_scores(self) -> list[float]:
        
        self.scores = [self.get_score_by_chunk(chunk_num) for chunk_num in self.encoded_document_by_chunks]
        
        return self.scores


In [ ]:
vmodel = SentenceTransformer('intfloat/multilingual-e5-large-instruct')
client = clickhouse_connect.get_client(host='localhost', port=8123, username='default', password='')

id_q = 1
for url in urls:
    try:
        doc = DocumentHolder(url)
        encoder = Encoder(doc.text, vmodel)
        encoder.encode_document()
        for k, v in encoder.encoded_text_by_pages.items():
            data = [[np.uint32(id_q), str(url), np.uint32(k), np.array(v), encoder.text_by_pages[k]]]
            set_to_db(client, data)
        id_q += 1
    except Exception as ex:
        print(ex)

In [ ]:
cross_encoder = CrossEncoder("intfloat/multilingual-e5-large")
for query in querys:
  scores = {}
  for text in texts:
    score = cross_encoder.predict([query, text])
    scores[score] = text

In [ ]:
torch.set_num_threads(4)
MODEL_PATH = "FRED-T5-large"

class Model:
    """
    Класс для работы с моделью, включая инициализацию и кодирование запросов.

    Args:
    client : объект
        Объект для работы с базой данных.
    llm_model : объект, по умолчанию T5 модель
        Модель для генерации текста.
    tokenizer_model : объект, по умолчанию GPT2Tokenizer модель
        Токенизатор модели для обработки текста.
    embedding_model : объект, по умолчанию SentenceTransformer модель
        Модель для кодирования запросов.

    Attributes:
    client : объект
        Объект для работы с базой данных.
    llm_model : объект
        Модель для генерации текста.
    tokenizer_model : объект
        Токенизатор модели для обработки текста.
    embedding_model : объект
        Модель для кодирования запросов.
    scores_by_documents : словарь
        Словарь для хранения оценок по документам.
    query : str
        Запрос.

    Methods:
    get_row(document_id, chunk_number) -> объект:
        Возвращает строку из базы данных по заданному идентификатору документа и номеру части.
    encode_query(query: str) -> list[float]:
        Кодирует запрос и возвращает список чисел с плавающей запятой.
    """
    def __init__(self, 
                 client,
                 llm_model = T5ForConditionalGeneration.from_pretrained(os.path.dirname(os.path.realpath("")) + f"/RussiaBank/models/{MODEL_PATH}"), 
                 tokenizer_model = GPT2Tokenizer.from_pretrained(os.path.dirname(os.path.realpath("")) + f"/RussiaBank/models//{MODEL_PATH}",eos_token='</s>'),
                 embedding_model = SentenceTransformer('intfloat/multilingual-e5-large-instruct')) -> None:
        self.client = client
        self.llm_model = llm_model
        self.tokenizer_model = tokenizer_model
        self.embedding_model = embedding_model
        self.scores_by_documents = {}
        self.query = ""
        
    def get_row(self, document_id, chunk_number):
        
        return self.client.command(f"SELECT * FROM document WHERE id = {document_id} AND chunk_number = {chunk_number}")

    def encode_query(self, query: str) -> list[float]:
        
        return self.embedding_model.encode(query)

    def calculate_similarities(self, query: str):
        """
        Метод для вычисления сходства между запросом и документами.
    
        Args:
        query : str
            Запрос.
    
        Returns:
        None
        """

        self.query = query
        
        count_docs: int = self.client.command(f"SELECT COUNT(DISTINCT id) FROM document")
        
        encoded_query: list[float] = self.encode_query(query)
        
        for id in range(1, count_docs + 1):
        
            self.scores_by_documents[id] = []
            
            count_chunks: int = self.client.command(f"SELECT COUNT(DISTINCT chunk_number) FROM document WHERE id = {id}")
            
            for chunk_num in range(1, count_chunks + 1):
            
                chunk: list[float] = list(map(float,self.client.command(f"SELECT chunk_array FROM document WHERE id = {id} AND chunk_number = {chunk_num}")[1:-1].split(",")))
                
                self.scores_by_documents[id].append(self.get_score_by_chunk(encoded_query, chunk))
                                                
    def get_score_by_chunk(self, encoded_query: list[float], chunk: list[float]) -> float:
        """
        Метод для вычисления оценки сходства между закодированным запросом и частью документа.
        
        Args:
        encoded_query : list[float]
        Закодированный запрос.
        chunk : list[float]
        Часть документа.
        
        Returns:
        float
        Оценка сходства между запросом и частью документа.
        """

        return chunk @ encoded_query / np.linalg.norm(chunk)

    def get_top_k_chunks(self, k_: int = 10) -> list[tuple]:
        
        all_chunk_scores: list[int] = []
        
        for i in list(self.scores_by_documents.values()):
        
            all_chunk_scores.extend(i)
        
        all_chunk_indices_scores_sorted: list[int] = np.argsort(all_chunk_scores)[::-1][:k_]

        dict_: dict[int, list[int]] = {}
        
        indx: int = 0
        
        for k in self.scores_by_documents:
        
            dict_[k] = []
            
            for i in range(len(self.scores_by_documents[k])):
            
                dict_[k].append(indx)
                
                indx += 1

        k_top_chunks_in_docs: list[tuple[int,int]] = []
        
        for key in dict_:
            
            for val in all_chunk_indices_scores_sorted:
            
                if val in dict_[key]:
                
                    temp: tuple[int,int] = (key,dict_[key].index(val))
                    
                    k_top_chunks_in_docs.append(temp)
        
        return k_top_chunks_in_docs

    def get_top_k_chunks_texts(self, k: int = 10) -> list[str]:
        
        k_top_chunks_in_docs: list[tuple[int,int]] = self.get_top_k_chunks()
        
        res = []
        
        for i in range(k):
        
            id, chunk_number = k_top_chunks_in_docs[i][0], k_top_chunks_in_docs[i][1]
            
            res.append(self.client.command(f"SELECT chunk_text FROM document WHERE id = {id} AND chunk_number = {chunk_number+1}"))    
        
        return res
    
    def FredT5(self,ninp: str,p={
            "do_sample":True,
            "top_p":0.9,
            "temperature":0.05,
            "repetition_penalty": 2.0,
            "min_length": 5,
            "max_length": 200,
            "tokens_offset":0
            }) -> str:
        ninp = f"""Сформулируй ответ на основании контекста Вопрос: '{self.query}', Контекст: '{ninp}'"""
        
        inp = ninp
        input_ids=torch.tensor([self.tokenizer_model.encode(inp,add_special_tokens=True)])
        outputs=self.llm_model.generate(input_ids,do_sample = p["do_sample"],top_p = p["top_p"],temperature=p["temperature"],repetition_penalty = p["repetition_penalty"],min_length = p["min_length"],max_length = p["max_length"],eos_token_id=self.tokenizer_model.encode(']',add_special_tokens=True)[0])#tokenizer.eos_token_id 
        
        return self.tokenizer_model.decode(outputs[0][1+p["tokens_offset"]:], skip_special_tokens=True) 


In [ ]:
client = clickhouse_connect.get_client(host='localhost', port=8123, username='default', password='')
model = Model(client)


In [ ]:
model.calculate_similarities("Че с ебалом? Мать жива?")


In [ ]:
for text in model.get_top_k_chunks_texts():
    print("_____________________________________________________________________")
    print(text)
    print("_____________________________________________________________________")
    print(model.FredT5(text))    